# Live Air Quality Index (AQI)

Sanjeev - Data-Alchemist

Imports:

In [ ]:
#%run ../aqi_dashboard/utils/get_aqi_data.py
import json
import os
import pandas as pd
import plotly.express as px
from sqlalchemy import create_engine
import utils.queries as q
#import streamlit_app as st
import streamlit_app_with_sidebar_tabs as st
from utils.get_aqi_data import run_query
from utils.state_map import map_state_names
from dotenv import load_dotenv
load_dotenv(dotenv_path='.streamlit/')

2025-07-11 13:58:06.172 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.173 No runtime found, using MemoryCacheStorageManager
2025-07-11 13:58:06.174 No runtime found, using MemoryCacheStorageManager
2025-07-11 13:58:06.175 No runtime found, using MemoryCacheStorageManager
2025-07-11 13:58:06.176 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.177 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.177 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.178 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.178 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-07-11 13:58:06.17

False

### Connect with Snowflake & Load data

In [10]:
user = os.getenv("SNOWFLAKE_USER")
password = os.getenv("SNOWFLAKE_PASSWORD")
account = os.getenv("SNOWFLAKE_ACCOUNT")
warehouse = os.getenv("SNOWFLAKE_WAREHOUSE")
database = os.getenv("SNOWFLAKE_DATABASE")
schema = os.getenv("SNOWFLAKE_SCHEMA")

engine = create_engine(
    f'snowflake://{user}:{password}@{account}/{database}/{schema}?warehouse={warehouse}'
)

Defaults

In [21]:
year = 2025
month = 3

def get_filtered_monthly_data(df, year, month):
    return df[(df["year"] == year) & (df["month"] == month)].sort_values(by="aqi", ascending=False)

def get_filtered_yearly_data(df, year):
    return df[(df["year"] == year)].sort_values(by="aqi", ascending=False)

In [22]:
selected_month = month
selected_year = year
with open("./utils/india_states.geojson", "r") as f:
    india_geo = json.load(f)
df_aqi_per_state = run_query(q.get_aqi_data_per_state)
# map state names to what geojson expects
df_aqi_per_state = map_state_names(df_aqi_per_state)

df_aqi_data = run_query(q.get_latest_aqi_data)    
year_list = sorted(df_aqi_per_state["year"].unique().tolist(), reverse=True)

# Filter the data
df_monthly_aqi_per_state = get_filtered_monthly_data(df_aqi_per_state, selected_year, selected_month)
df_yearly_aqi_per_state = get_filtered_yearly_data(df_aqi_per_state, selected_year)

In [ ]:

df_aqi_per_state = run_query(q.get_aqi_data_per_state)
df_aqi_diff = st.compute_monthly_aqi_change(df_aqi_per_state)
df_selected = df_aqi_diff[
            (df_aqi_diff["year"] == selected_year) & (df_aqi_diff["month"] == selected_month)
        ].dropna(subset=["aqi_change"])
# new_df = df_aqi_diff[(df_aqi_diff["year"] == selected_year) & (df_aqi_diff["month"] == selected_month)]
# new_df
# Sort and get top/bottom 5
top5_worsened = df_selected.nlargest(5, "aqi_pct_change")
top5_improved = df_selected.nsmallest(5, "aqi_pct_change")

# Combine and mark
highlight_df = pd.concat([top5_worsened, top5_improved])
st.plot_aqi_change_bar(highlight_df)

KeyError: 'aqi_pct_change'

Prep for visualizations

## Plots

### Heatmap

In [13]:
st.make_heatmap(df_yearly_aqi_per_state, 'month', 'state_for_map', 'aqi', st.selected_color_theme)

alt.LayerChart(...)

### Choropleth

In [14]:
st.make_choropleth_india(df_monthly_aqi_per_state, st.selected_color_theme, selected_month)